In [1]:
from ckonlpy.tag import Twitter
import pickle
import re
import sys
from gensim.models import TfidfModel
from gensim.models import Word2Vec
from gensim.corpora import Dictionary
from pprint import pprint
from collections import Counter
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import mglearn
from pprint import pprint
from ckonlpy.tag import Twitter
import numpy as np
import gc

class Social_analysis():
    
    non_bmp_map = dict.fromkeys(range(0x10000, sys.maxunicode + 1), 0xfffd)

    def __init__(self):
        self.twitter = Twitter()
        
    def pickle_to_table(self, filename):
        with open(filename, 'rb') as f:
            data = pickle.load(f)
        data = data[1:]
        for idx, i in enumerate(data):
            data[idx][2] = i[2].replace('#', ' ').translate(self.non_bmp_map)
            data[idx][3] = '/'.join(i[3])
            data[idx][4] = '/'.join(i[4])
        self.raw_data = np.array(data)
  
    def hashtags_split(self, hashtags):        
        hashtags_split = []
        for i in hashtags:
            hashtags_split.append(i.split('/'))
        
        hashtags_list = []
        
        for i in hashtags_split:
            temp = []
            for j in i:
                if self.isHangul(j):
                    t_hashtags = j.translate(self.non_bmp_map)
                    temp.append(t_hashtags)
            hashtags_list.append(temp)
        self.hashtags_list = hashtags_list
        
        return hashtags_list
            

        
    def add_keyword_dic(self, keyword_list, tag='Noun'):
        for i in keyword_list:
            if type(i) == tuple:
                self.twitter.add_dictionary(i[0], i[1])
            else:
                self.twitter.add_dictionary(i, tag)
        
    def morph_pos(self, text_list, exception_list = ['맛', '밥', '물', '몸']):
        
        morph_list = []
        noun_list = []
        adj_list = []
        verb_list = []
        
        for j in text_list:
            parsed = self.twitter.pos(j)
            temp = []
            n_temp = []
            adj_temp = []
            verb_temp = []
            
            for i in parsed:
                if self.isHangul(i[0]):
                    if (len(i[0]) > 1) or (i[0] in exception_list):
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                        elif i[1] == 'Verb':
                            adj_temp.append(i[0])
                        elif i[1] == 'Adjective':
                            verb_temp.append(i[0])
                    else:
                        print('{} 제외'.format(i[0]))
                else: print('{} 한글이 아님.'.format(i[0]))
            

            morph_list.append(temp)
            noun_list.append(n_temp)
            adj_list.append(adj_temp)
            verb_list.append(verb_temp)

        nav_list = noun_list + adj_list + verb_list

        return morph_list, nav_list, noun_list, adj_list, verb_list

    def merge_list(self, tokenized_list):
        return [j for i in tokenized_list for j in i]

    
    def join_list(self, tokenized_list):
        joined_list = []
        for idx, i in enumerate(tokenized_list):
            joined_list.append(" ".join(i))
        return joined_list
 
    def split_list(self, untokenized_list):
        hashtag_splited = []
        for idx, i in enumerate(untokenized):
            hashtag_splited.append(i.split('/'))
            return hastag_splited

    def word_substitute(self, dataset, sublist):
        dataset = dataset
        sub_book = dict()
        for i in sublist:
            for j in i['sub_words']:
                sub_book[j] = i['main']
        gc.collect()
        for n, i in enumerate(dataset):
            dataset[n] = [sub_book.get(item,item) for item in i]

        del sub_book
        gc.collect()

        return dataset
    
    def word_delete(dataset, del_list):
        dataset = dataset

        for n, line in enumerate(dataset):
             dataset[n] = [i for i in line if i not in del_list]

        return dataset

    
    def isHangul(self, text):
        encText = text
        hanCount = len(re.findall(u'[\u3130-\u318F\uAC00-\uD7A3]+', encText))
        return hanCount > 0

    

class SB_Word2Vec():    
    
    def __init__(self, morph_list):
        self.dct = Dictionary(morph_list)
        self.corpus = [self.dct.doc2bow(line) for line in morph_list]
        self.build_Word2Vec(morph_list)
    
    def make_Word2Vec(self, morph_list, size=50, window=2, min_count=10, iteration=100):
        self.em = Word2Vec(morph_list, size=size, window=window, min_count=min_count, iter=iteration)
        self.em_vocab = list(self.em.wv.vocab.keys())
        self.em_vocab_dic = {word:idx for idx, word in enumerate(self.em_vocab)}

    def make_Word2Sen_matrix(self): 
        vocab_size = len(self.em_vocab)
        self.sen_matrix = np.zeros((len(self.corpus), vocab_size))
        for idx, row in enumerate(self.sen_matrix):
            for idx2, frequency in self.corpus[idx]:
                    if self.dct[idx2] in self.em_vocab:
                        self.sen_matrix[idx][self.em_vocab_dic[self.dct[idx2]]] = frequency                
        self.sim_matrix = np.zeros((vocab_size, vocab_size))
        for idx, w1 in enumerate(self.em_vocab):
            for idx2, w2 in enumerate(self.em_vocab):
                self.sim_matrix[idx][idx2] =  self.em.wv.similarity(w1, w2)

        self.word2sen_matrix = np.dot(self.sim_matrix, np.transpose(self.sen_matrix))

        return self.word2sen_matrix

    def get_sim_sen(self, keyword, main_text, number=1):
        self.sim_sen_index = np.argsort(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        self.most_sim_sen_index = np.argmax(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        index_list = self.sim_sen_index.reshape((-1,)).tolist()
        index_list.reverse()
        
        for idx, i in enumerate(index_list[:number]):
            print(str(idx + 1))
            print(main_text[i])
        return index_list
    
    def build_Word2Vec(self, morph_list):
        self.make_Word2Vec(morph_list)
        self.make_Word2Sen_matrix()
        
        
class SB_LDA():

    def make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20):        
        self.vect = CountVectorizer(max_features=10000, max_df=.15)
        self.X = self.vect.fit_transform(morph_joined)
        self.lda = LatentDirichletAllocation(n_components=ntopic, learning_method=learning_method, max_iter=max_iter, random_state=random_state)
        self.document_topics = self.lda.fit_transform(self.X)
        self.sorting = np.argsort(self.lda.components_, axis=1)[:, ::-1]
        self.feature_names = np.array(self.vect.get_feature_names())
        mglearn.tools.print_topics(topics=range(ntopic), feature_names=self.feature_names, sorting=self.sorting, topics_per_chunk=5, n_words=n_words)

    def related_doc(self, main_text_list, topic_index, number=10):
        category = np.argsort(self.document_topics[:, topic_index])[::-1]
        related_docs = []
        for i in category[:number]:
            print(i)
            print(main_text_list[i] + ".\n")
            related_docs.append((i, main_text_list[i]))
        return related_docs

class SB_Tfidf():    
    
    def __init__(self, list_morph_merged):
        self.list_morph_merged = list_morph_merged
        self.dct = Dictionary(self.list_morph_merged)
        self.corpus = [self.dct.doc2bow(line) for line in self.list_morph_merged]

    def get_tfidf(self):       
        self.model = TfidfModel(self.corpus)
        self.tfidf = []
        for i in self.corpus:
             self.tfidf.append(sorted(self.model[i], key = lambda x: x[1], reverse=True))
        self.tfidf_hangul = []
        for idx1, i in enumerate(self.tfidf):
            self.tfidf_hangul.append([(self.dct[j[0]], j[1]) for j in i])        
        
        return self.tfidf_hangul
    
def frequency(merged):
    word_count = Counter(merged)
    word_count2 = []
    for i in word_count:
        word_count2.append((i, word_count[i]))
    word_count2 = sorted(word_count2, key=lambda x: x[1], reverse = True)
    return word_count2

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
intake = Social_analysis()

## DB에서 불러온 데이터를 Social_analysis 인스턴스에 등록해도  되고,  그냥 그 데이터로 앞으로 진행해도 된다. 일단 튜토리얼은 pickle 데이터로 진행하기 때문에 아래 함수를 실행하면 intake.row_data 에 저장이 된다. 이 놈은 DB에 들어간 놈이 비슷하게 생긴 놈이다.

In [3]:
intake.pickle_to_table('Data/intake_list.txt')

## 형태소 분석에 꼭 포함하고 싶은 단어를 추가한다. 기본적으로는 hashtag들을 noun으로 추가한다. 여기서 해쉬태그 중에 포함하고 싶지 않은 것을 빼는 것을 추천한다.

In [4]:
hashtag_splited = intake.hashtags_split(intake.raw_data[:, 3])
print(np.shape(hashtag_splited))
print(hashtag_splited[0])

(5235,)
['아침식사', '죽', '모닝죽', '단호박', '인테이크', '맛스타그램', '먹스타그램', '식사대용', '다이어트', '두통', '좋아요반사', '맛집', '간편식', '아점', '아픔', '선팔은맞팔', '맛스타', '선팔', '맞팔', '먹스타', '음식', '푸드스타그램', '좋반']


## intake.add_dic_keyword() 함수는 1차원 list를 받는다.
## 데이터의 형태는 ['단어', '단어', '단어'] or [('단어', Tag), ('단어', Tag)]
## Tag는 'Noun', 'Verb', 'Adjective' 등이 있다.

In [5]:
hashtag_merged = intake.merge_list(hashtag_splited)

In [6]:
intake.add_keyword_dic(hashtag_splited)

## 형태소 분석을 진행한다.

In [7]:
morph_list, nav_list, noun_list, adj_list, verb_list= intake.morph_pos(intake.raw_data[:, 2])

lora는 한글이 아님.
.는 한글이 아님.
study는 한글이 아님.
죽는 제외
.는 한글이 아님.
몇는 제외
년는 제외
째는 제외
먹는 제외
는는 제외
엔는 제외
하는 제외
고는 제외
도는 제외
데는 제외
면는 제외
�는 한글이 아님.
가는 제외
데는 제외
..는 한글이 아님.
다는 제외
랑는 제외
가는 제외
오는 제외
�는 한글이 아님.
1122는 한글이 아님.
_는 한글이 아님.
asm는 한글이 아님.
.는 한글이 아님.
고는 제외
,는 한글이 아님.
.는 한글이 아님.
먹는 제외
을는 제외
수는 제외
수는 제외
요는 제외
!는 한글이 아님.
는는 제외
일는 제외
요는 제외
.는 한글이 아님.
감는 제외
있는 제외
게는 제외
!는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
makemysugar는 한글이 아님.
.는 한글이 아님.
한는 제외
잔는 제외
�는 한글이 아님.
!는 한글이 아님.
~~는 한글이 아님.
먹는 제외
는는 제외
것는 제외
가는 제외
틈는 제외
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
oats는 한글이 아님.
oatmeal는 한글이 아님.
oasis는 한글이 아님.
_는 한글이 아님.
jaeyoon는 한글이 아님.
짜는 제외
죽는 제외
.는 한글이 아님.
로는 제외
다는 제외
.는 한글이 아님.
이는 제외
.는 한글이 아님.
khjhmom는 한글이 아님.
_는 한글이 아님.
을는 제외
워는 제외
시는 제외
기는 제외
�는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
ㅎ는 제외
leeminwk는 한글이 아님.
차는 제외
받는 제외
음는 제외
.는 한글이 아님.
은는 제외
만는 제외
한는 제외
질는 제외
vveun는 한글이 아님.
제는 제외
술는 제외
안는 제외
��는 한글이 아님.
_는 한글이 아님.
si는 한글이 아님.
1는 한글이 아님.
ver는 한글이 아님.
_는 한글이 아님.
star는 한글이 아

marina는 한글이 아님.
_는 한글이 아님.
dieter는 한글이 아님.
20180703는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
�는 한글이 아님.
+는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
�‍♀️는 한글이 아님.
�는 한글이 아님.
무는 제외
나는 제외
�는 한글이 아님.
�는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
(@intakefoods는 한글이 아님.
)는 한글이 아님.
다는 제외
!는 한글이 아님.
먹는 제외
가는 제외
에는 제외
데는 제외
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
샐는 제외
러는 제외
리는 제외
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
이는 제외
.는 한글이 아님.
도는 제외
해는 제외
라는 제외
..는 한글이 아님.
�는 한글이 아님.
데는 제외
좀는 제외
더는 제외
!는 한글이 아님.
이는 제외
감는 제외
이는 제외
없는 제외
음는 제외
!는 한글이 아님.
한는 제외
형는 제외
이는 제외
!는 한글이 아님.
�는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
INTAKE는 한글이 아님.
apub는 한글이 아님.
_는 한글이 아님.
meal는 한글이 아님.
_는 한글이 아님.
chk는 한글이 아님.
다는 제외
가는 제외
서는 제외
이는 제외
젠는 제외
를는 제외
까는 제외
!는 한글이 아님.
옆는 제외
고는 제외
들는 제외
덕는 제외
에는 제외
가는 제외
다는 제외
가는 제외
....는 한글이 아님.
야는 제외
하는 제외
...는 한글이 아님.
고는 제외
나는 제외
봐는 제외
!!는 한글이 아님.
좀는 제외
!!는 한글이 아님.
�는 한글이 아님.
하는 제외
고는 제외
쳤는 제외
때는 제외
을는 제외
듯는 제외
�는 한글이 아님.
lovely는 한글이 아님.
__는 한글이 아님.
eu

caris는 한글이 아님.
_는 한글이 아님.
pakSBS는 한글이 아님.
이는 제외
서는 제외
한는 제외
3는 한글이 아님.
및는 제외
로는 제외
1000는 한글이 아님.
3는 한글이 아님.
^^는 한글이 아님.
에는 제외
랑는 제외
씩는 제외
...는 한글이 아님.
빨는 제외
아는 제외
...는 한글이 아님.
할는 제외
때는 제외
했는 제외
...는 한글이 아님.
안는 제외
네는 제외
...는 한글이 아님.
난는 제외
가는 제외
...는 한글이 아님.
뭐는 제외
의는 제외
은는 제외
...는 한글이 아님.
니는 제외
!!는 한글이 아님.
hwayoung는 한글이 아님.
2000는 한글이 아님.
·는 한글이 아님.
·는 한글이 아님.
중는 제외
�는 한글이 아님.
줄는 제외
하는 제외
는는 제외
은는 제외
에는 제외
량는 제외
덜는 제외
고는 제외
�는 한글이 아님.
!!는 한글이 아님.
가는 제외
149는 한글이 아님.
kcal는 한글이 아님.
라는 제외
�는 한글이 아님.
이는 제외
게는 제외
??는 한글이 아님.
???는 한글이 아님.
·는 한글이 아님.
·는 한글이 아님.
·는 한글이 아님.
intakefoods는 한글이 아님.
[는 한글이 아님.
인는 제외
X는 한글이 아님.
]는 한글이 아님.
,는 한글이 아님.
!는 한글이 아님.
1는 한글이 아님.
등는 제외
과는 제외
1는 한글이 아님.
등는 제외
이는 제외
!는 한글이 아님.
신는 제외
이는 제외
될는 제외
지는 제외
요는 제외
❛˓◞˂̵✧는 한글이 아님.
도는 제외
로는 제외
겟는 제외
할는 제외
지는 제외
요는 제외
zonemad는 한글이 아님.
도는 제외
:-)는 한글이 아님.
식는 제외
so는 한글이 아님.
.는 한글이 아님.
y는 한글이 아님.
_는 한글이 아님.
94는 한글이 아님.
건는 제외
행는 제외
�는 한글이 아님.
hssun는 한글이 아님.
24는 한글이 아님.
를는 제외
다는 제외
고는 제외
의는 제외
은는 제외
뭘는 제외
야는 제외
하는 제외
나는 제외
가는 제외
을는

marathon는 한글이 아님.
sports는 한글이 아님.
sportsman는 한글이 아님.
runningman는 한글이 아님.
d는 한글이 아님.
.는 한글이 아님.
myday는 한글이 아님.
_는 한글이 아님.
1027는 한글이 아님.
�는 한글이 아님.
2018는 한글이 아님.
.는 한글이 아님.
06는 한글이 아님.
.는 한글이 아님.
23는 한글이 아님.
�는 한글이 아님.
:는 한글이 아님.
,는 한글이 아님.
,는 한글이 아님.
:는 한글이 아님.
꿀는 제외
죽는 제외
,는 한글이 아님.
:는 한글이 아님.
:는 한글이 아님.
밤는 제외
,는 한글이 아님.
2는 한글이 아님.
-는 한글이 아님.
는는 제외
배는 제외
가는 제외
서는 제외
다는 제외
못는 제외
어는 제외
욥는 제외
.는 한글이 아님.
이는 제외
집는 제외
에는 제외
가는 제외
놨는 제외
!!!!!는 한글이 아님.
!!!!!는 한글이 아님.
이는 제외
거는 제외
인는 제외
서는 제외
어는 제외
욥는 제외
.는 한글이 아님.
에는 제외
옷는 제외
만는 제외
걸는 제외
뎁는 제외
��는 한글이 아님.
의는 제외
힘는 제외
은는 제외
내는 제외
욥는 제외
.는 한글이 아님.
-는 한글이 아님.
고는 제외
과는 제외
하는 제외
게는 제외
에는 제외
어는 제외
욥는 제외
.는 한글이 아님.
까는 제외
욥는 제외
.는 한글이 아님.
은는 제외
어는 제외
욥는 제외
.는 한글이 아님.
야는 제외
게는 제외
쬽는 제외
?는 한글이 아님.
들는 제외
뛰는 제외
었는 제외
네는 제외
욥는 제외
��는 한글이 아님.
-는 한글이 아님.
➡️는 한글이 아님.
못는 제외
되는 제외
면는 제외
는는 제외
뎁는 제외
여는 제외
욥는 제외
.는 한글이 아님.
youngbin는 한글이 아님.
.는 한글이 아님.
sim는 한글이 아님.
2018는 한글이 아님.
.는 한글이 아님.
6는 한글이 아님.
.는 한글이 아님.
23는 한글이 아님.
.는 한글이 아님.
런는 제외
x는 한글이 아님.
��는 한글이 아님.
에는

d는 한글이 아님.
.는 한글이 아님.
myday는 한글이 아님.
_는 한글이 아님.
1027는 한글이 아님.
�는 한글이 아님.
2018는 한글이 아님.
.는 한글이 아님.
06는 한글이 아님.
.는 한글이 아님.
21는 한글이 아님.
�는 한글이 아님.
진는 제외
와는 제외
의는 제외
이는 제외
에는 제외
욥는 제외
��는 한글이 아님.
는는 제외
게는 제외
라는 제외
에는 제외
욥는 제외
.는 한글이 아님.
가는 제외
서는 제외
했는 제외
네는 제외
욥는 제외
.는 한글이 아님.
을는 제외
때는 제외
이는 제외
큰는 제외
한는 제외
다는 제외
고는 제외
하는 제외
휴는 제외
찌는 제외
고는 제외
이는 제외
했는 제외
어는 제외
욥는 제외
!는 한글이 아님.
에는 제외
욥는 제외
��는 한글이 아님.
-는 한글이 아님.
이는 제외
졌는 제외
게는 제외
야는 제외
겠는 제외
어는 제외
욥는 제외
.는 한글이 아님.
과는 제외
가는 제외
더는 제외
욥는 제외
.는 한글이 아님.
초는 제외
큼는 제외
들는 제외
도는 제외
좋는 제외
겠는 제외
어는 제외
욥는 제외
.는 한글이 아님.
나는 제외
,,는 한글이 아님.
,는 한글이 아님.
고는 제외
~는 한글이 아님.
욥는 제외
내는 제외
.는 한글이 아님.
-는 한글이 아님.
➡️는 한글이 아님.
칭는 제외
테는 제외
도는 제외
보는 제외
었는 제외
이는 제외
놈는 제외
안는 제외
샀는 제외
을는 제외
거는 제외
욥는 제외
.는 한글이 아님.
dekerbell는 한글이 아님.
내는 제외
!!!!!!!!!는 한글이 아님.
왜는 제외
도는 제외
말는 제외
안는 제외
�는 한글이 아님.
???????는 한글이 아님.
daily는 한글이 아님.
lunch는 한글이 아님.
diet는 한글이 아님.
intake는 한글이 아님.
food는 한글이 아님.
jmt는 한글이 아님.
31는 한글이 아님.
centimeter는 한글이 아님.
인는 제외
당는 제외
랑는 제외
해는 제외
은는 제외
걸는 제외
로는 제외
쟁는 제외
여는 제외

...

intakefoods는 한글이 아님.
밤는 제외
에는 제외
먹는 제외
는는 제외
한는 제외
이는 제외
있는 제외
!는 한글이 아님.
를는 제외
@6am_corner는 한글이 아님.
님는 제외
!는 한글이 아님.
・・・는 한글이 아님.
밤는 제외
에는 제외
먹는 제외
는는 제외
�는 한글이 아님.
데는 제외
아는 제외
.는 한글이 아님.
는는 제외
는는 제외
분는 제외
,는 한글이 아님.
이는 제외
신는 제외
분는 제외
들는 제외
을는 제외
위는 제외
한는 제외
을는 제외
다는 제외
!는 한글이 아님.
.는 한글이 아님.
는는 제외
><는 한글이 아님.
.는 한글이 아님.
죽는 제외
hyeleeyo는 한글이 아님.
�는 한글이 아님.
intakefoods는 한글이 아님.
눈는 제외
!!는 한글이 아님.
를는 제외
주는 제외
신는 제외
@cherry_jooo는 한글이 아님.
님는 제외
!!는 한글이 아님.
・・・는 한글이 아님.
.는 한글이 아님.
☃는 한글이 아님.
눈는 제외
한는 제외
�는 한글이 아님.
�는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
는는 제외
는는 제외
분는 제외
,는 한글이 아님.
이는 제외
신는 제외
분는 제외
들는 제외
을는 제외
위는 제외
한는 제외
을는 제외
다는 제외
!는 한글이 아님.
.는 한글이 아님.
는는 제외
><는 한글이 아님.
.는 한글이 아님.
죽는 제외
diet는 한글이 아님.
_는 한글이 아님.
balmoxx는 한글이 아님.
2015는 한글이 아님.
.는 한글이 아님.
12는 한글이 아님.
.는 한글이 아님.
9는 한글이 아님.
-는 한글이 아님.
85는 한글이 아님.
g는 한글이 아님.
것는 제외
1는 한글이 아님.
2는 한글이 아님.
1는 한글이 아님.
/는 한글이 아님.
3는 한글이 아님.
큰는 제외
1는 한글이 아님.
5는 한글이 아님.
2는 한글이 아님.
장는 제외
것는 제외
,는 한글이 아님.
...는 한글이 아님.
200는 한글이 아님.
ml는 한글이 아님.
것는 제외
1는 한글이 아님.
4

diet는 한글이 아님.
_는 한글이 아님.
balmoxx는 한글이 아님.
2015는 한글이 아님.
.는 한글이 아님.
11는 한글이 아님.
.는 한글이 아님.
23는 한글이 아님.
-는 한글이 아님.
1는 한글이 아님.
/는 한글이 아님.
2는 한글이 아님.
1는 한글이 아님.
/는 한글이 아님.
2는 한글이 아님.
(는 한글이 아님.
브는 제외
200는 한글이 아님.
ml는 한글이 아님.
)는 한글이 아님.
1는 한글이 아님.
-는 한글이 아님.
1는 한글이 아님.
.는 한글이 아님.
에는 제외
후는 제외
!는 한글이 아님.
은는 제외
나는 제외
밤는 제외
+는 한글이 아님.
계는 제외
흰는 제외
거는 제외
�는 한글이 아님.
나는 제외
했는 제외
었는 제외
.는 한글이 아님.
낮는 제외
간는 제외
꿀는 제외
!는 한글이 아님.
2는 한글이 아님.
.는 한글이 아님.
전는 제외
+는 한글이 아님.
인는 제외
줄는 제외
많는 제외
나는 제외
이는 제외
에는 제외
요는 제외
!!는 한글이 아님.
내는 제외
각는 제외
�는 한글이 아님.
3는 한글이 아님.
.는 한글이 아님.
먹는 제외
게는 제외
,는 한글이 아님.
,는 한글이 아님.
가는 제외
때는 제외
되는 제외
면는 제외
빵는 제외
도는 제외
한는 제외
입는 제외
만는 제외
서는 제외
고는 제외
...는 한글이 아님.
딱는 제외
의는 제외
을는 제외
<는 한글이 아님.
X는 한글이 아님.
,는 한글이 아님.
X는 한글이 아님.
,는 한글이 아님.
제는 제외
X는 한글이 아님.
>는 한글이 아님.
로는 제외
그는 제외
외는 제외
을는 제외
게는 제외
나는 제외
을는 제외
것는 제외
서는 제외
을는 제외
했는 제외
.는 한글이 아님.
의는 제외
,는 한글이 아님.
,는 한글이 아님.
는는 제외
서는 제외
!는 한글이 아님.
과는 제외
안는 제외
하는 제외
을는 제외
써는 제외
야는 제외
겠는 제외
요는 제외
.는 한글이 아님.
에는 제외
제는 제외
개는 제외
했는 제외
!는 한글이 아님.
데는 제외
서는 제외

와는 제외
다는 제외
.는 한글이 아님.
쬐는 제외
~는 한글이 아님.
끔는 제외
만는 제외
더는 제외
하는 제외
는는 제외
...는 한글이 아님.
ㅋ는 제외
은는 제외
별는 제외
개는 제외
에는 제외
별는 제외
네는 제외
?는 한글이 아님.
����✨는 한글이 아님.
_는 한글이 아님.
yoo는 한글이 아님.
.는 한글이 아님.
hana는 한글이 아님.
517는 한글이 아님.
.는 한글이 아님.
20151021는 한글이 아님.
�는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
는는 제외
다는 제외
끝는 제외
난는 제외
아는 제외
더는 제외
을는 제외
것는 제외
�는 한글이 아님.
다는 제외
히는 제외
히는 제외
님는 제외
들는 제외
잘는 제외
자는 제외
요는 제외
:-)는 한글이 아님.
������는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
diet는 한글이 아님.
dietfood는 한글이 아님.
DANO는 한글이 아님.
_는 한글이 아님.
_는 한글이 아님.
_는 한글이 아님.
��는 한글이 아님.
jinajina는 한글이 아님.
0624는 한글이 아님.
들는 제외
.는 한글이 아님.
용는 제외
데는 제외
잘는 제외
쓰는 제외
고는 제외
.는 한글이 아님.
들는 제외
♡는 한글이 아님.
가는 제외
될는 제외
게는 제외
diet는 한글이 아님.
.는 한글이 아님.
heeee는 한글이 아님.
2015는 한글이 아님.
.는 한글이 아님.
10는 한글이 아님.
.는 한글이 아님.
21는 한글이 아님.
+는 한글이 아님.
22는 한글이 아님.
일는 제외
:는 한글이 아님.
50는 한글이 아님.
.는 한글이 아님.
1는 한글이 아님.
kg는 한글이 아님.
:는 한글이 아님.
:는 한글이 아님.
,는 한글이 아님.
2는 한글이 아님.
개는 제외
(는 한글이 아님.
1는 한글이 아님.
만는 제외
),는 한글이 아님.
:는 한글이 아님.
거는 제외
2는 한글이 아님.
개는 제외
,는 한글이 아님.
1는 한글이 아님.
개는 제외
,는

awpmotors는 한글이 아님.
_는 한글이 아님.
revokorea는 한글이 아님.
뉴는 제외
S는 한글이 아님.
3는 한글이 아님.
2는 한글이 아님.
.는 한글이 아님.
0는 한글이 아님.
T는 한글이 아님.
킷는 제외
된는 제외
지는 제외
되는 제외
지는 제외
뉴는 제외
S는 한글이 아님.
3는 한글이 아님.
2는 한글이 아님.
.는 한글이 아님.
0는 한글이 아님.
T는 한글이 아님.
이는 제외
인는 제외
킷는 제외
장는 제외
(는 한글이 아님.
ECU는 한글이 아님.
는는 제외
후는 제외
^^)는 한글이 아님.
200는 한글이 아님.
km는 한글이 아님.
한는 제외
급는 제외
다는 제외
.는 한글이 아님.
AWP는 한글이 아님.
와는 제외
도는 제외
다는 제외
^^는 한글이 아님.
ecu는 한글이 아님.
와는 제외
시는 제외
의는 제외
을는 제외
주는 제외
며는 제외
인는 제외
들는 제외
과는 제외
의는 제외
을는 제외
다는 제외
.는 한글이 아님.
2015는 한글이 아님.
년는 제외
식는 제외
ecu는 한글이 아님.
로는 제외
revo는 한글이 아님.
에는 제외
오는 제외
는는 제외
다는 제외
^^는 한글이 아님.
◆는 한글이 아님.
AWP는 한글이 아님.
와는 제외
이는 제외
고는 제외
무는 제외
을는 제외
선는 제외
다는 제외
.는 한글이 아님.
의는 제외
는는 제외
로는 제외
도는 제외
이는 제외
을는 제외
수는 제외
있는 제외
.는 한글이 아님.
12는 한글이 아님.
:는 한글이 아님.
무는 제외
,는 한글이 아님.
24는 한글이 아님.
연는 제외
3는 한글이 아님.
%~는 한글이 아님.
,는 한글이 아님.
36는 한글이 아님.
연는 제외
4는 한글이 아님.
%~는 한글이 아님.
:는 한글이 아님.
-는 한글이 아님.
02는 한글이 아님.
)는 한글이 아님.
578는 한글이 아님.
-는 한글이 아님.
8090는 한글이 아님.
,는 한글이 아님.
:는 한글이 아님.
010는 한글이 아님.
-는 한글이 아님.
3631는 한글이 아님.
-는 한

your는 한글이 아님.
10는 한글이 아님.
x는 한글이 아님.
10는 한글이 아님.
_는 한글이 아님.
_는 한글이 아님.
지는 제외
말는 제외
.는 한글이 아님.
이는 제외
게는 제외
.는 한글이 아님.
:는 한글이 아님.
)는 한글이 아님.
_는 한글이 아님.
'는 한글이 아님.
죽는 제외
'는 한글이 아님.
/는 한글이 아님.
/는 한글이 아님.
www.10x10.co.kr/1294226는 한글이 아님.
_는 한글이 아님.
10는 한글이 아님.
x는 한글이 아님.
10는 한글이 아님.
tenbyten는 한글이 아님.
intake는 한글이 아님.
죽는 제외
shinhancard는 한글이 아님.
_는 한글이 아님.
official는 한글이 아님.
daily는 한글이 아님.
point는 한글이 아님.
blackandwhite는 한글이 아님.
bw는 한글이 아님.
inkwell는 한글이 아님.
-는 한글이 아님.
게는 제외
면는 제외
요는 제외
-는 한글이 아님.
와는 제외
엔는 제외
에는 제외
!는 한글이 아님.
주는 제외
실는 제외
?는 한글이 아님.
:)는 한글이 아님.
-는 한글이 아님.
ama는 한글이 아님.
5117는 한글이 아님.
이는 제외
거는 제외
고는 제외
.는 한글이 아님.
....는 한글이 아님.
꿀는 제외
+는 한글이 아님.
가는 제외
��는 한글이 아님.
에는 제외
먹는 제외
을는 제외
거는 제외
.는 한글이 아님.
에는 제외
이는 제외
거는 제외
!는 한글이 아님.
.는 한글이 아님.
.는 한글이 아님.
food는 한글이 아님.
diet는 한글이 아님.
dietfood는 한글이 아님.
healthyfood는 한글이 아님.
eating는 한글이 아님.
eat는 한글이 아님.
instafood는 한글이 아님.
yummy는 한글이 아님.
instafood는 한글이 아님.
dietdiary는 한글이 아님.
cleanfood는 한글이 아님.
ragoni는 한글이 아님.
.는 한글이 아님.
shineun는 한글이 아님.
superbar는 한글

In [10]:
hashtag_splited = intake.hashtags_split(intake.raw_data[:, 3])

In [11]:
raw_list = [morph_list, nav_list, noun_list, adj_list, verb_list] + hashtag_splited

## 빈도분석에는 merge된 list가 필요하다.

In [12]:
nav_merged = intake.merge_list(nav_list)

In [13]:
'맛' in nav_list

False

In [23]:
nav_frequency = frequency(nav_merged)

In [24]:
nav_frequency [:5]

[('인테이크', 5727), ('다이어트', 2167), ('밀스', 1490), ('아침', 1273), ('모닝죽', 1212)]

## 여기서 내가 형태소분석시에 안짤리게 할 단어와 제외하고 싶은 단어, 대체하고 싶은 단어를 선택한다.
## 안짤리게 할 단어는 다시 위로 돌아가 추가한다.
## 대체하고 싶은 단어와 제외하고 싶은 단어는 아래 방법으로 처리한다. 일단 생략한다.

### 토픽모델링은 조인된 것이 필요하다.
### join_list 를 통해서 만들기

In [25]:
morph_joined = intake.join_list(nav_list)

### 파라미터는 다음과 같다. 
#### self.make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20)
#### ntopic과 n_words를 넣어주면 몇개의 토픽으로 나눌지, 몇개의 단어를 보여줄지를 정할 수 있다.

In [60]:
intake.LDA = SB_LDA()
intake.LDA.make_lda(morph_joined, ntopic=10)

topic 0       topic 1       topic 2       topic 3       topic 4       
--------      --------      --------      --------      --------      
모닝죽           힘내            있는            다이어트          건강            
아침            운동            많은            저녁            다이어트          
일상            시켜            입니            다이어터          구매            
먹스타그램         않아            있어            점심            먹스타그램         
다이어트          먹겠            같아            들어오시          맛스타그램         
단호박           타서            이벤트           다이어트그램        링크            
간식            주문했           씨씨앙           1개            데일리           
고구마           않는            아니            먹고            유산균           
데일리           씹어            괜찮            받은            건강식           
맛스타그램         드시            없는            사과            후기            
소통            찍어            있다            함께하는          선물            
단호박죽          정모            참여            고구마           간식            
식단조절  

### 그 토픽과 관련된 문서 10개를 보여준다. 두번째 인자는 토픽의 인덱스이고 세번째 인덱스는 보여줄 포스팅의 개수이다.

In [61]:
topic0 = intake.LDA.related_doc(intake.raw_data[:,2], 0, 4)

88
d.myday_1027�2018.06.26�
아침 : 곤약젤리
점심 : 현미밥, 부대찌개
저녁 : 곤약젤리
간식 : 참외1개, 순살치킨꼬치
-
오늘부터 장마래서 아침 일찍 운동 나가려고 했는데 이미 장마는 시작되었어욥. 덕분에 얼리버드로 간만에 8시에 아침을 먹었어욥. 다 좋은데 배가 너무 빨리 고파져욥.
-
오늘 갑자기 먹신님이 오셔서 병원 다녀오는 길에 편의점을 들렸어욥. 부대찌개만 사려고 했는데 포스기 옆에 치킨들이 나를 불렀어욥. 결심했어욥. 우리집에 데려가기로. 그 장맛비를 뚫고 무사히 사와서 무사히 헤치웠어욥. 부대찌개는 라면사리만 열심히 건져먹고 햄은 매늬 남았어욥. 내일 먹을거에욥. 점심을 옴총 잘먹었더니 하루종일 배가 불러서 저녁은 가볍게 패스할 수 있을 줄 알았어욥. 정확히 여덟시 오십분에 곤약젤리 꺼냈어욥.
-
참외는 씹어먹어야 맛나는건줄 알았는데 이번에 사온 참외가 맛이 없는 거였어욥.
-
➡️ 그나저나 이 비들 실화에욥? 난 비오는 날 외출이 제일 시럽��.

4238
a1dana1004� 견과류 대부분이 두뇌회전에도 좋고~
다이어트, 노화예방등에도 좋다죠~
요즘 웰빙시대에
견과류는 일부러 챙겨드시는 분들이
점점 더 늘고 계신것 같아요!

매일매일  하루견과
그래서 다가오는  추석선물
 견과류선물 좋은것 같아요!

남녀노소 누구나할것없이
어린이들부터 어르신들까지
누구나 즐길 수 있는  선물1순위

 인테이크  닥터넛츠
선물하기도 좋은 고급스런 패키지

괜찮죠?^^  선물세트 추석선물세트  간식스타그램  간식그램  영양간식  간식타임  어린이간식  술안주  맥주안주  안주스타그램 맛있다그램  맛있다  식사대용  먹방스타그램  먹스타그램  건강스타그램  건강그램  건강  가족건강  nuts  gift  건강간식  영양간식.

3995
love_07.30몸이 무거울땐 가볍게 먹자고 주문한건데_
이건뭐 간식수준_ �
 식사대용 아침밥대신 가볍게 먹을라한건데
맛있잖아 _ 양이 너무 작아 결국 컵라면 뜯었음
딸램이도 두봉이나 흡입 _ 더 시키

### 데이터 형식은 같고 할 줄 알겠지?

In [32]:
intake.SB_word2vec = SB_Word2Vec(nav_list)

In [33]:
intake.flavor = intake.SB_word2vec.get_sim_sen('모닝죽', intake.raw_data[:,2], 4)

1
intakefoods귀차니즘 한방에 해결! 한끼 식사대용으로 굿❤️ 미래식사
.
후기남겨주신 @sundaenge.dd 님 감사합니다!
・・・
 아침식단 D+166 160112 아침 6:50
 긴글주의  읽으면복받음
.
 인테이크  선식  밀스  밀스오리지널
.
.
얼마전에 받은 밀스로 오늘 아침은 간단하게�(사실 어제 밤 8시에 케이크먹은�) 밀스에 대한 설명과 후기 작성할께요�
.
.
 인테이크설명 � @intakefoods
� 완전한  미래식사 누구나 꿈꿔왔던 빠르고 완전한식사
.
 구성 (1일영양소기준치에대한비율)
탄수화물 57%(33가지곡류채소로구성)
단백질 20%(식물성 단백질 대두분리 단백질과 동물성인 유청분리 단백질조합) � 23g
지방 15%(아몬드파우더)
식이섬유 5% 미네랄 프로바이오틱스 비타민 각1%
.
.
 선댕이후기 �
맛은 제가 지금까지 먹어본 선식들보다 맛있어요� 전 처음엔 무조건 물에 타 먹어보거든요 밀스는 물에 타먹어도 거부감 없고 미숫가루 먹는 느낌~!(저의 기준입니다☺) 그리고 안에 뭔가 씹히는게 견과류쪽인거 같은데 마시는 끝까지 씹혀서 먹는재미도 쏠쏠~ 그리고 끼니마다 단백질등 영양성분에 예민한 저에겐 저기 영양성분표를 보고 완전 마음에 들었네요��� 사실 대중에 있는 선식엔 영양성분표가 없는게 너무 아쉬웠거든요�
그래서 맛이있어도 저희 오빠 간식용으로 먹이는� 그리고 보틀에 포장되어 있으니 와우� 짱 편함�� 다만 역시나 선식은 비싸서� 오빠랑 이구동성으로 싸면 쟁여놓고 싶다고 말했네요�(선식은 좋은재료가 많이들어가니 어쩔수없고�) 아~! 제가 느끼는 포만감은 10:40분(6시50분먹음) 배가 고파지기시작~ 생각보다 포만감이 오래감� 우유나 두유에 타먹으면 더 오래갈듯☺
.
.
 깨알오빠후기 �
지금까지 먹어본거 중 제일 맛있고 씹히는게 많아서 좋아� 포만감도 좋구만~(참고로 저희오빠는 선식을 간식으로 드셔요� 오빠는  소이카페 에 타드심)
.
.
긴글읽어주신 여러분 오늘 행복만땅 지방타파 하루되실꺼에용���
.
.
 

## TFIDF에는 merge 된 리스트를 넣어서 비교해주면 된다. 
## intake만 있어서 패스
## 토픽모델링 된 애들끼리 비교해보는 것도 좋을 듯.

In [ ]:
tfidf = SB_Tfidf([intake.morph_merged, labnosh.morph_merged, meals.morph_merged, morningjuk.morph_merged, easy_food.morph_merged, conven_food.morph_merged])

tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

In [1]:
labnosh = Social_analysis('labnosh.txt', 'labnosh.official')

meals = Social_analysis('meals.txt', 'intakefoods')

morningjuk = Social_analysis('morningjuk.txt', 'intakefoods')

easy_food = Social_analysis('easy_food.txt')

conven_food = Social_analysis('conven_food.txt')

keywords = [intake, labnosh, meals, morningjuk, easy_food, conven_food]

### 빈도분석

for i in keywords:
    print(len(i.main_text_list), len(i.morph_merged))

labnosh.morph_frequency = analyzer.frequency(labnosh.morph_merged)
pprint(labnosh.morph_frequency)

meals.morph_frequency = analyzer.frequency(meals.morph_merged)
pprint(meals.morph_frequency)

morningjuk.morph_frequency = analyzer.frequency(morningjuk.morph_merged)
pprint(morningjuk.morph_frequency)

easy_food.morph_frequency = analyzer.frequency(easy_food.morph_merged)
pprint(easy_food.morph_frequency)

conven_food.morph_frequency = analyzer.frequency(conven_food.morph_merged)
pprint(conven_food.morph_frequency)

### 토픽모델링

intake.LDA = analyzer.SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=10)

topic0 = intake.LDA.related_doc(intake.main_text_list, 0)

topic1 = intake.LDA.related_doc(intake.main_text_list, 1)

topic2 = intake.LDA.related_doc(intake.main_text_list, 2)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)

topic7 = intake.LDA.related_doc(intake.main_text_list, 7)

topic9 = intake.LDA.related_doc(intake.main_text_list, 9)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)



labnosh.LDA = analyzer.SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=10)

meals.LDA = analyzer.SB_LDA()
meals.LDA.make_lda(meals.morph_joined, ntopic=10)

morningjuk.LDA = analyzer.SB_LDA()
morningjuk.LDA.make_lda(morningjuk.morph_joined, ntopic=10)

easy_food.LDA = analyzer.SB_LDA()
easy_food.LDA.make_lda(easy_food.morph_joined, ntopic=10)

conven_food.LDA = analyzer.SB_LDA()
conven_food.LDA.make_lda(conven_food.morph_joined, ntopic=10)

### Word2Vec

intake.SB_word2vec = analyzer.SB_Word2Vec(intake.hashtags_appended)

intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.main_hash_dic, intake.main_text_list, 4)


intake.diet = intake.SB_word2vec.get_sim_sen('다이어트', intake.main_hash_dic, intake.main_text_list, 4)


intake.health = intake.SB_word2vec.get_sim_sen('건강', intake.main_hash_dic, intake.main_text_list, 4)


intake.exercise = intake.SB_word2vec.get_sim_sen('운동', intake.main_hash_dic, intake.main_text_list, 4)


intake.morningjuk = intake.SB_word2vec.get_sim_sen('모닝죽', intake.main_hash_dic, intake.main_text_list, 4)


intake.meals = intake.SB_word2vec.get_sim_sen('밀스', intake.main_hash_dic, intake.main_text_list, 4)


intake.gonyak = intake.SB_word2vec.get_sim_sen('곤약젤리', intake.main_hash_dic, intake.main_text_list, 4)




### TFIDF

tfidf = analyzer.SB_Tfidf([intake.morph_merged, labnosh.morph_merged, meals.morph_merged, morningjuk.morph_merged, easy_food.morph_merged, conven_food.morph_merged])

tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

meals_juk_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, morningjuk.morph_merged])

tfidf_meals_juk = meals_juk_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_juk:
    pprint(i[:10])
    print()

intake_meals_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, meals.morph_merged])

tfidf_intake_meals = intake_meals_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_meals:
    pprint(i[:10])
    print()

intake_morningjuk_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, morningjuk.morph_merged])

tfidf_intake_morningjuk = intake_morningjuk_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_morningjuk:
    pprint(i[:10])
    print()

meals_conven_food_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, conven_food.morph_merged])

tfidf_meals_conven_food = meals_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

morningjuk_conven_food_SB_Tfidf = analyzer.SB_Tfidf([morningjuk.morph_merged, conven_food.morph_merged])

tfidf_morningjuk_conven_food = morningjuk_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [9]:
import csv
with open('morph_list.csv', 'w', encoding='utf-8') as f:
    spamwriter = csv.writer(f, delimiter=' ',
                            quotechar='|', quoting=csv.QUOTE_MINIMAL)
    for i in intake.morph_list:
        spamwriter.writerow(i)

In [16]:
def morph_pos(text_list, add_list, del_list, exception_list = ['맛', '밥', '물', '몸']):
    morph_list = []
    noun_list = []
    adj_list = []
    verb_list = []

    for j in text_list:
        parsed = self.twitter.pos(j)
        temp = []
        n_temp = []
        adj_temp = []
        verb_temp = []

        for i in parsed:
            if self.isHangul(i):
                if not i[0] in del_list:
                    if len(i[0]) > 1:
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                        elif i[1] == 'Verb':
                            n_adj.append(i[0])
                        elif i[1] == 'Adjective':
                            n_verb.append(i[0])

                    elif i in exception_list:
                        temp.append(i)
            else: print(i, '한글이 아닙니다.')

        morph_list.append(temp)
        noun_list.append(n_temp)
        adj_list.append(adj_temp)
        verb_list.append(verb_temp)


    nav_list = noun_list + adj_list + verb_list

    return morph_list, nav_list, noun_list, adj_list, verb_list

In [ ]:

    '''def get_from_dic(self, filename):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.dataset_dic, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_dic(self.data)

        # dataset, main_text_list, morph_list, morph_merged, morph_joined, hashtags_merged, hashtags_appended, main_hash_dic
    def get_data_from_list(self, filename, add_list, del_list):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_list(self.data[1:], add_list, del_list)'''
